In [1]:
import os, glob, re, io, random, gensim, smart_open, logging
import numpy as np

from PyPDF2 import PdfReader
from pdfminer.high_level import extract_text as fallback_text_extraction
from gensim.models.doc2vec import Doc2Vec, TaggedDocument
from gensim.test.utils import get_tmpfile
from nltk.tokenize import word_tokenize


In [2]:
pdfReaders = []
pdfFiles = []
docLabels = []

# taggedData = []
# wordSets = []

logging.basicConfig(format='%(asctime)s : %(levelname)s : %(message)s', level=logging.INFO)
rootDir = "/Users/tillman/t-root/dev/projects/2022/pdf-correlator/gitignored"
txtExtractDir = "/Users/tillman/t-root/dev/projects/2022/pdf-correlator/gitignored/txt-extractions/"
zoteroDir = '/Users/tillman/t-root/zotero/storage'

stoplist = set('for a of the and to in'.split(' '))

In [3]:
# read files
def read_files():
    os.chdir(rootDir)
    for file in glob.glob("**/*.pdf"):
        pdfFiles.append(file)
        pdfReaders.append(PdfReader(file))
    print("pdf files read")
            
read_files()

pdf files read


In [4]:
print(pdfReaders)

[<PyPDF2._reader.PdfReader object at 0x107d7efb0>, <PyPDF2._reader.PdfReader object at 0x107da1990>, <PyPDF2._reader.PdfReader object at 0x1629017b0>, <PyPDF2._reader.PdfReader object at 0x162902920>, <PyPDF2._reader.PdfReader object at 0x162902b30>, <PyPDF2._reader.PdfReader object at 0x162902980>, <PyPDF2._reader.PdfReader object at 0x162902aa0>, <PyPDF2._reader.PdfReader object at 0x162902bc0>, <PyPDF2._reader.PdfReader object at 0x162901720>, <PyPDF2._reader.PdfReader object at 0x162941270>, <PyPDF2._reader.PdfReader object at 0x162941240>, <PyPDF2._reader.PdfReader object at 0x162941060>, <PyPDF2._reader.PdfReader object at 0x162941180>, <PyPDF2._reader.PdfReader object at 0x1629420e0>, <PyPDF2._reader.PdfReader object at 0x1629420b0>, <PyPDF2._reader.PdfReader object at 0x1629421a0>, <PyPDF2._reader.PdfReader object at 0x162942950>, <PyPDF2._reader.PdfReader object at 0x162942ad0>, <PyPDF2._reader.PdfReader object at 0x162942e00>]


In [5]:
print(pdfFiles[13])

pdf-tests/Lai - 2020 - KafkaReimagined – A Non-Linear Reinterpretation i.pdf


In [6]:
def extract_to_txt():
    os.chdir(txtExtractDir)
    pat0 = ('(?<!Dr)(?<!Esq)\. +(?=[A-Z])')
    pat1 = ('\.+(?=[A-Z])')
    pat2 = ('\.+(?=[0-9])')
    pat3 = ('\. +(?=[0-9])')
    pat4 = ('(?=[for a of the and to in])')
    
    patterns = [pat0, pat1, pat2, pat3, pat4]
    counter = 0
    for i in pdfReaders:
        counter += 1
        print(counter)
        with open(str([i.metadata.title]) + ".txt", 'w', encoding="utf-8") as file:
            
            # add doc title to array for reference / tagging
            docLabels.append(i.metadata.title)
            print(i.metadata.title)
            try:
                for j in range(len(i.pages)):
                    # format txt file so that each line is one sentence (doc2vec requirement)
                    text = i.getPage(j).extract_text()
                    text = re.sub(patterns[0], '.\n', text)
                    text = re.sub(patterns[1], '.\n', text)
                    text = re.sub(patterns[2], '.\n', text)
                    text = re.sub(patterns[3], '.\n', text)
                    text = re.sub(patterns[4], '', text)
                    file.write(text)   
#                     print(j)
                    
            except Exception as exc:
                    print(">>>>> exception")
                    # format txt file so that each line is one sentence (doc2vec requirement)
                    text = fallback_text_extraction(rootDir + "/" + pdfFiles[counter])
                    text = re.sub(patterns[0], '.\n', text)
                    text = re.sub(patterns[1], '.\n', text)
                    text = re.sub(patterns[2], '.\n', text)
                    text = re.sub(patterns[3], '.\n', text)
                    text = re.sub(patterns[4], '', text)
                    file.write(text)   


extract_to_txt()
# print("extracted files labeled: " + str(docLabels))



1
Arts and design as translational mechanisms for academic entrepreneurship_ The metaLAB at Harvard case study
2
pone.0099019 1..8
3
None
4
User attention and behaviour in virtual reality art encounter
5
Microsoft Word - CHI2018_LucidDreaming_v5.docx
6
Microsoft Word - 48710116.DOC
7
frvir-2022-779148 1..5
8
Making Art Therapy Virtual: Integrating Virtual Reality Into Art Therapy With Adolescents
9
None
10
Making Art Therapy Virtual: Integrating Virtual Reality Into Art Therapy With Adolescents
11
Microsoft Word - LeavingVR_Finals.docx
12
ShareVR: Enabling Co-Located Experiences for Virtual Reality between HMD and Non-HMD Users
13
None
>>>>> exception
14
Kafka:Reimagined – A Non-Linear Reinterpretation in VR
15
The effects of visual context and individual differences on perception and evaluation of modern art and graffiti art
16
IAFOR Journal of Cultural Studies – Volume 6 – Issue 1 
17
g5grap.lo
18
User attention and behaviour in virtual reality art encounter
19
ShareVR: Enabling Co-L

In [7]:
class CorpusGen(object):
    def __init__(self, dirname):
        self.dirname = dirname
 
    def __iter__(self, tokens_only=False):
        for fname in os.listdir(self.dirname):
            with smart_open.open(fname, encoding="iso-8859-1") as f:
                for i, line in enumerate(f):
                    tokens = gensim.utils.simple_preprocess(line, min_len=2, max_len=15, deacc=True)
                    if tokens_only:
                        yield tokens
                    else:
                        yield gensim.models.doc2vec.TaggedDocument(tokens, [i])

trainCorpus = list(CorpusGen('/Users/tillman/t-root/dev/projects/2022/pdf-correlator/gitignored/txt-extractions'))


print(list(trainCorpus))

[TaggedDocument(words=['contents', 'lists', 'available', 'atsciencedirect'], tags=[0]), TaggedDocument(words=['journal', 'of', 'business', 'research'], tags=[1]), TaggedDocument(words=['journal', 'homepage', 'www', 'elsevier', 'com', 'locate', 'jbusres'], tags=[2]), TaggedDocument(words=['arts', 'and', 'design', 'as', 'translational', 'mechanisms', 'for', 'academic', 'the', 'metalab', 'at', 'harvard', 'case', 'study'], tags=[3]), TaggedDocument(words=['luca', 'simeonea', 'giustina', 'secundob', 'giovanni', 'schiumac'], tags=[4]), TaggedDocument(words=['adepartment', 'of', 'architecture', 'design', 'and', 'media', 'technology', 'aalborg', 'university'], tags=[5]), TaggedDocument(words=[], tags=[6]), TaggedDocument(words=['meyers', 'va', 'nge', 'ka', 'benhavn', 'sv', 'denmark'], tags=[7]), TaggedDocument(words=['bdepartment', 'of', 'innovation', 'engineering', 'university', 'of', 'salento', 'lecce', 'italy'], tags=[8]), TaggedDocument(words=['cdepartment', 'of', 'mathematics', 'informati

In [8]:
# class MyCorpus:
#     def __iter__(self):
#         for line in open('/Users/tillman/t-root/dev/projects/2022/pdf-correlator/gitignored/txt-extractions/new-dark-age.txt'):
#             # assume there's one document per line, tokens separated by whitespace
#             yield dictionary.doc2bow(line.lower().split())
                
# trainCorpus = MyCorpus()

# print(list(trainCorpus))
    

In [9]:
# def read_corpus(fname, tokens_only=False):
        
#     with smart_open.open(fname, encoding="iso-8859-1") as f:
#         for i, line in enumerate(f):
#             tokens = gensim.utils.simple_preprocess(line)
#             if tokens_only:
#                 yield tokens
#             else:
#                 yield gensim.models.doc2vec.TaggedDocument(tokens, [i])

In [10]:
# with open(txtExtractDir + 'fullcorpus.txt', 'w+') as file:
#     for items in sentences:
#         file.writelines('%s\n' %items)

In [11]:
# trainCorpus = list(read_corpus('/Users/tillman/t-root/dev/projects/2022/pdf-correlator/gitignored/txt-extractions/new-dark-age.txt'))
    
# print(trainCorpus)

In [12]:
# train the model

model = gensim.models.doc2vec.Doc2Vec(vector_size=50, min_count=2, epochs=40)
model.build_vocab(trainCorpus)


2022-09-27 10:11:00,768 : INFO : Doc2Vec lifecycle event {'params': 'Doc2Vec<dm/m,d50,n5,w5,mc2,s0.001,t3>', 'datetime': '2022-09-27T10:11:00.768004', 'gensim': '4.2.0', 'python': '3.10.6 | packaged by conda-forge | (main, Aug 22 2022, 20:41:22) [Clang 13.0.1 ]', 'platform': 'macOS-12.0.1-arm64-arm-64bit', 'event': 'created'}
2022-09-27 10:11:00,768 : INFO : collecting all words and their counts
2022-09-27 10:11:00,768 : INFO : PROGRESS: at example #0, processed 0 words (0 words/s), 0 word types, 0 tags
2022-09-27 10:11:00,780 : INFO : PROGRESS: at example #10000, processed 76666 words (6595137 words/s), 11430 word types, 0 tags
2022-09-27 10:11:00,792 : INFO : collected 22721 word types and 3552 unique tags from a corpus of 15933 examples and 171706 words
2022-09-27 10:11:00,793 : INFO : Creating a fresh vocabulary
2022-09-27 10:11:00,809 : INFO : Doc2Vec lifecycle event {'msg': 'effective_min_count=2 retains 9624 unique words (42.36% of original 22721, drops 13097)', 'datetime': '202

In [13]:
# check word occurence
print(f"Word 'the' appeared {model.wv.get_vecattr('the', 'count')} times in the training corpus.")

Word 'the' appeared 10475 times in the training corpus.


In [14]:
model.train(trainCorpus, total_examples=model.corpus_count, epochs=model.epochs)

2022-09-27 10:11:00,886 : INFO : Doc2Vec lifecycle event {'msg': 'training model with 3 workers on 9624 vocabulary and 50 features, using sg=0 hs=0 sample=0.001 negative=5 window=5 shrink_windows=True', 'datetime': '2022-09-27T10:11:00.886950', 'gensim': '4.2.0', 'python': '3.10.6 | packaged by conda-forge | (main, Aug 22 2022, 20:41:22) [Clang 13.0.1 ]', 'platform': 'macOS-12.0.1-arm64-arm-64bit', 'event': 'train'}
2022-09-27 10:11:01,226 : INFO : EPOCH 0: training on 171706 raw words (141049 effective words) took 0.3s, 421091 effective words/s
2022-09-27 10:11:01,549 : INFO : EPOCH 1: training on 171706 raw words (141099 effective words) took 0.3s, 443974 effective words/s
2022-09-27 10:11:01,858 : INFO : EPOCH 2: training on 171706 raw words (141055 effective words) took 0.3s, 463469 effective words/s
2022-09-27 10:11:02,164 : INFO : EPOCH 3: training on 171706 raw words (141121 effective words) took 0.3s, 469031 effective words/s
2022-09-27 10:11:02,465 : INFO : EPOCH 4: training o

In [15]:
# infer a vector from corupus (I dont actually know what this means or does! :D )
vector = model.infer_vector(['only', 'you', 'can', 'prevent', 'forest', 'fires'])
print("infering a vector:")
print(vector)

infering a vector:
[-0.07972852  0.15404777  0.3715676  -0.1474573  -0.05287993  0.18500553
 -0.07813589  0.02753361 -0.30286053 -0.04885469  0.05750459 -0.10492019
  0.10111783 -0.296329   -0.18583888  0.11170213 -0.03972993 -0.29781216
 -0.09141926 -0.07954276 -0.02649403  0.18158701  0.27826038  0.2254627
 -0.1364038  -0.0004608   0.03528284  0.11884583 -0.08717355  0.12578882
  0.08196942  0.28473404  0.34701476  0.0446377  -0.18683259  0.13787444
  0.12835707 -0.20276588 -0.01194392  0.1091178   0.4225353  -0.06288571
  0.07681289 -0.29234564  0.2260954   0.23259984 -0.13091399 -0.0134539
 -0.00485572 -0.04340826]


In [16]:
print(list(trainCorpus))

[TaggedDocument(words=['contents', 'lists', 'available', 'atsciencedirect'], tags=[0]), TaggedDocument(words=['journal', 'of', 'business', 'research'], tags=[1]), TaggedDocument(words=['journal', 'homepage', 'www', 'elsevier', 'com', 'locate', 'jbusres'], tags=[2]), TaggedDocument(words=['arts', 'and', 'design', 'as', 'translational', 'mechanisms', 'for', 'academic', 'the', 'metalab', 'at', 'harvard', 'case', 'study'], tags=[3]), TaggedDocument(words=['luca', 'simeonea', 'giustina', 'secundob', 'giovanni', 'schiumac'], tags=[4]), TaggedDocument(words=['adepartment', 'of', 'architecture', 'design', 'and', 'media', 'technology', 'aalborg', 'university'], tags=[5]), TaggedDocument(words=[], tags=[6]), TaggedDocument(words=['meyers', 'va', 'nge', 'ka', 'benhavn', 'sv', 'denmark'], tags=[7]), TaggedDocument(words=['bdepartment', 'of', 'innovation', 'engineering', 'university', 'of', 'salento', 'lecce', 'italy'], tags=[8]), TaggedDocument(words=['cdepartment', 'of', 'mathematics', 'informati

In [17]:
# assessing the model
ranks = []
secondRanks = []
for doc_id in range(len(trainCorpus)):
        inferredVector = model.infer_vector(trainCorpus[doc_id].words)
        sims = model.dv.most_similar([inferredVector], topn=len(model.dv))
        rank = [docid for docid, sim in sims].index(doc_id)
        ranks.append(rank)
        print(doc_id)
        
        secondRanks.append(sims[1])

0
1
2
3
4
5
6
7
8
9
10
11
12
13
14
15
16
17
18
19
20
21
22
23
24
25
26
27
28
29
30
31
32
33
34
35
36
37
38
39
40
41
42
43
44
45
46
47
48
49
50
51
52
53
54
55
56
57
58
59
60
61
62
63
64
65
66
67
68
69
70
71
72
73
74
75
76
77
78
79
80
81
82
83
84
85
86
87
88
89
90
91
92
93
94
95
96
97
98
99
100
101
102
103
104
105
106
107
108
109
110
111
112
113
114
115
116
117
118
119
120
121
122
123
124
125
126
127
128
129
130
131
132
133
134
135
136
137
138
139
140
141
142
143
144
145
146
147
148
149
150
151
152
153
154
155
156
157
158
159
160
161
162
163
164
165
166
167
168
169
170
171
172
173
174
175
176
177
178
179
180
181
182
183
184
185
186
187
188
189
190
191
192
193
194
195
196
197
198
199
200
201
202
203
204
205
206
207
208
209
210
211
212
213
214
215
216
217
218
219
220
221
222
223
224
225
226
227
228
229
230
231
232
233
234
235
236
237
238
239
240
241
242
243
244
245
246
247
248
249
250
251
252
253
254
255
256
257
258
259
260
261
262
263
264
265
266
267
268
269
270
271
272
273
274
275
276
27

1899
1900
1901
1902
1903
1904
1905
1906
1907
1908
1909
1910
1911
1912
1913
1914
1915
1916
1917
1918
1919
1920
1921
1922
1923
1924
1925
1926
1927
1928
1929
1930
1931
1932
1933
1934
1935
1936
1937
1938
1939
1940
1941
1942
1943
1944
1945
1946
1947
1948
1949
1950
1951
1952
1953
1954
1955
1956
1957
1958
1959
1960
1961
1962
1963
1964
1965
1966
1967
1968
1969
1970
1971
1972
1973
1974
1975
1976
1977
1978
1979
1980
1981
1982
1983
1984
1985
1986
1987
1988
1989
1990
1991
1992
1993
1994
1995
1996
1997
1998
1999
2000
2001
2002
2003
2004
2005
2006
2007
2008
2009
2010
2011
2012
2013
2014
2015
2016
2017
2018
2019
2020
2021
2022
2023
2024
2025
2026
2027
2028
2029
2030
2031
2032
2033
2034
2035
2036
2037
2038
2039
2040
2041
2042
2043
2044
2045
2046
2047
2048
2049
2050
2051
2052
2053
2054
2055
2056
2057
2058
2059
2060
2061
2062
2063
2064
2065
2066
2067
2068
2069
2070
2071
2072
2073
2074
2075
2076
2077
2078
2079
2080
2081
2082
2083
2084
2085
2086
2087
2088
2089
2090
2091
2092
2093
2094
2095
2096
2097
2098


3544
3545
3546
3547
3548
3549
3550
3551


ValueError: 3552 is not in list

In [ ]:
for i in range(len(trainCorpus)):
    print(i)

In [ ]:
import collections

counter = collections.Counter(ranks)
print(counter)


In [ ]:
print('Document ({}): «{}»\n'.format(doc_id, ' '.join(trainCorpus[doc_id].words)))
print(u'SIMILAR/DISSIMILAR DOCS PER MODEL %s:\n' % model)
for label, index in [('MOST', 0), ('SECOND-MOST', 1), ('MEDIAN', len(sims)//2), ('LEAST', len(sims) - 1)]:
    print(u'%s %s: «%s»\n' % (label, sims[index], ' '.join(trainCorpus[sims[index][0]].words)))